In [1]:
!rm -rf /content/*
!git clone https://github.com/urmzd/lepus-classifier

Cloning into 'lepus-classifier'...
remote: Enumerating objects: 1242, done.
remote: Counting objects: 100% (1242/1242), done.
remote: Compressing objects: 100% (778/778), done.
remote: Total 1242 (delta 707), reused 819 (delta 364), pack-reused 0
Receiving objects: 100% (1242/1242), 57.05 MiB | 7.21 MiB/s, done.
Resolving deltas: 100% (707/707), done.


In [2]:
!pip install wandb pytorch-lightning pipetools loguru typing_extensions
!pip install pyyaml==5.4.1

     |████████████████████████████████| 1.8 MB 4.2 MB/s 
     |████████████████████████████████| 582 kB 69.7 MB/s 
     |████████████████████████████████| 58 kB 7.6 MB/s 
     |████████████████████████████████| 181 kB 88.7 MB/s 
     |████████████████████████████████| 144 kB 92.9 MB/s 
     |████████████████████████████████| 63 kB 2.2 MB/s 
     |████████████████████████████████| 136 kB 77.9 MB/s 
     |████████████████████████████████| 398 kB 71.6 MB/s 
     |████████████████████████████████| 596 kB 84.1 MB/s 
     |████████████████████████████████| 1.1 MB 72.9 MB/s 
     |████████████████████████████████| 144 kB 82.7 MB/s 
     |████████████████████████████████| 94 kB 3.3 MB/s 
     |████████████████████████████████| 271 kB 91.0 MB/s 
  Created wheel for pipetools: filename=pipetools-1.1.0-py3-none-any.whl size=13621 sha256=9d4392dd41441a6cdd246beb5cf4deb717a9d64d62da9acbdb75d0479460d7f5
  Stored in directory: /root/.cache/pip/wheels/db/e4/55/098fde0def89ca29d2cf30f27b19e299c835ce2a0

In [3]:
!wandb login

wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter, or press ctrl+c to quit: 
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [4]:
import sys
SRC_PATH = "/content/lepus-classifier"
sys.path.insert(0, SRC_PATH)

###New Baseline

In [ ]:
from src.bootstrap import bootstrap, TrainerFactory, N_CLASSES
from src.data.data_handler import BasicModel, MetricsCallback
from pathlib import Path
from pytorch_lightning.loggers import WandbLogger
import wandb
import pytorch_lightning as pl
import torch
from torchmetrics import Accuracy
import torch.nn.functional as F

trainer_factory = TrainerFactory(
    strategy=None, 
    max_epochs=100, 
)

class BaseLine(BasicModel):
    def __init__(self, n_targets=2, learning_rate=0.001) -> None:
        super().__init__(n_targets,learning_rate)
        # Hyper Parameters

        self.layer_1 = torch.nn.Conv2d(1, 16, 2, 2)
        self.layer_2 = torch.nn.MaxPool2d(2, 2)
        self.layer_3 = torch.nn.ReLU()
        self.layer_4 = torch.nn.Conv2d(16, 32, 2, 2)
        self.layer_5 = torch.nn.MaxPool2d(2, 2)
        self.layer_6 = torch.nn.ReLU()
        self.layer_7 = torch.nn.Conv2d(32, 64, 2, 2)
        self.layer_8 = torch.nn.MaxPool2d(2, 2)
        self.layer_9 = torch.nn.ReLU()
        self.layer_10 = torch.nn.Dropout2d(0.2)
        self.layer_11 = torch.nn.Flatten(1, -1)
        self.layer_12 = torch.nn.Linear(64 * 3 * 3, n_targets)
        self.softmax_layer = torch.nn.LogSoftmax()

    def forward(self, x):
        x_1 = self.layer_1(x)
        x_2 = self.layer_2(x_1)
        x_3 = self.layer_3(x_2)
        x_4 = self.layer_4(x_3)
        x_5 = self.layer_5(x_4)
        x_6 = self.layer_6(x_5)
        x_7 = self.layer_7(x_6)
        x_8 = self.layer_8(x_7)
        x_9 = self.layer_9(x_8)
        x_10 = self.layer_10(x_9)
        x_11 = self.layer_11(x_10)
        x_12 = self.layer_12(x_11)
        result = self.softmax_layer(x_12)
        return result

bootstrap(trainer_factory=trainer_factory, data_manfiest_path=Path("/content/lepus-classifier/resources/data.csv"),
          model=BaseLine(), batch_size=8)

/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)
wandb: Currently logged in as: csci-4155-rabbit-classifier (use `wandb login --relogin` to force relogin)


Global seed set to 42
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

   | Name          | Type       | Params
----------------------------------------------
0  | layer_1       | Conv2d     | 80    
1  | layer_2       | MaxPool2d  | 0     
2  | layer_3       | ReLU       | 0     
3  | layer_4       | Conv2d     | 2.1 K 
4  | layer_5       | MaxPool2d  | 0     
5  | softmax_layer | LogSoftmax | 0     
6  | layer_6       | ReLU       | 0     
7  | layer_7       | Conv2d     | 8.3 K 
8  | layer_8       | MaxPool2d  | 0     
9  | layer_9       | ReLU       | 0     
10 | layer_10      | Dropout2d  | 0     
11 | layer_11      | Flatten    | 0     
12 | layer_12      | Linear     | 1.2 K 
----------------------------------------------
11.6 K    Trainable params
0         Non-trainable params
11.6 K    Total params
0.046     Total estimated model params si

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:48: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.


Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

###Width01: Increase of filter quantity

In the baseline model, we noticed sizable gaps between training accuracy and validation accuracy for several of the folds. To reduce this, we decided to increase the number of filters in each convolution layer of the model. The rationale behind this is to increase the number of patterns in the data the model can recognize.

In [5]:
from src.bootstrap import bootstrap, TrainerFactory, N_CLASSES
from src.data.data_handler import BasicModel, MetricsCallback
from pathlib import Path
from pytorch_lightning.loggers import WandbLogger
import wandb
import pytorch_lightning as pl
import torch
from torchmetrics import Accuracy
import torch.nn.functional as F

trainer_factory = TrainerFactory(
    strategy=None, 
    max_epochs=100, 
)

class Width01(BasicModel):
    def __init__(self, n_targets=2, learning_rate=0.001) -> None:
        super().__init__(n_targets,learning_rate)
        # Hyper Parameters

        self.layer_1 = torch.nn.Conv2d(1, 32, 2, 2)
        self.layer_2 = torch.nn.MaxPool2d(2, 2)
        self.layer_3 = torch.nn.ReLU()
        self.layer_4 = torch.nn.Conv2d(32, 64, 2, 2)
        self.layer_5 = torch.nn.MaxPool2d(2, 2)
        self.layer_6 = torch.nn.ReLU()
        self.layer_7 = torch.nn.Conv2d(64, 128, 2, 2)
        self.layer_8 = torch.nn.MaxPool2d(2, 2)
        self.layer_9 = torch.nn.ReLU()
        self.layer_10 = torch.nn.Dropout2d(0.2)
        self.layer_11 = torch.nn.Flatten(1, -1)
        self.layer_12 = torch.nn.Linear(128 * 3 * 3, n_targets)
        self.softmax_layer = torch.nn.LogSoftmax()

    def forward(self, x):
        x_1 = self.layer_1(x)
        x_2 = self.layer_2(x_1)
        x_3 = self.layer_3(x_2)
        x_4 = self.layer_4(x_3)
        x_5 = self.layer_5(x_4)
        x_6 = self.layer_6(x_5)
        x_7 = self.layer_7(x_6)
        x_8 = self.layer_8(x_7)
        x_9 = self.layer_9(x_8)
        x_10 = self.layer_10(x_9)
        x_11 = self.layer_11(x_10)
        x_12 = self.layer_12(x_11)
        result = self.softmax_layer(x_12)
        return result

bootstrap(trainer_factory=trainer_factory, data_manfiest_path=Path("/content/lepus-classifier/resources/data.csv"),
          model=Width01(), batch_size=8)

/usr/local/lib/python3.7/dist-packages/distributed/config.py:20: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  defaults = yaml.load(f)
wandb: Currently logged in as: csci-4155-rabbit-classifier (use `wandb login --relogin` to force relogin)


Global seed set to 42
GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
wandb: logging graph, to disable use `wandb.watch(log_graph=False)`
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

   | Name          | Type       | Params
----------------------------------------------
0  | layer_1       | Conv2d     | 160   
1  | layer_2       | MaxPool2d  | 0     
2  | layer_3       | ReLU       | 0     
3  | layer_4       | Conv2d     | 8.3 K 
4  | layer_5       | MaxPool2d  | 0     
5  | softmax_layer | LogSoftmax | 0     
6  | layer_6       | ReLU       | 0     
7  | layer_7       | Conv2d     | 32.9 K
8  | layer_8       | MaxPool2d  | 0     
9  | layer_9       | ReLU       | 0     
10 | layer_10      | Dropout2d  | 0     
11 | layer_11      | Flatten    | 0     
12 | layer_12      | Linear     | 2.3 K 
----------------------------------------------
43.6 K    Trainable params
0         Non-trainable par

Training: 0it [00:00, ?it/s]

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:48: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.


Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

Testing: 0it [00:00, ?it/s]

The addition of more filters, though having increased validation accuracy, mildly decreased the test accuracy in comparison to the baseline model. This may be due to the fact that the greater size of the resultant tensor did not include valuable information that wouold assist the model in clasifying between a rabbit and a hare.